In [ ]:
# !pip install emot
# !pip install symspellpy
# !pip install setuptools wheel
# !pip install spacy
# !pip install pyspellchecker
# !pip install spellchecker
# !pip install inflect
# !pip install langdetect
# !pip install google_trans_new
# !pip install deep-translator
# !pip install ekphrasis
# !pip install cdifflib
# !pip install gensim
# !pip install wordninja

In [1]:
import nltk
from nltk.corpus import PlaintextCorpusReader
import re, string, json

from symspellpy.symspellpy import SymSpell, Verbosity
import pkg_resources
import spacy
from tqdm.notebook import tqdm
from spellchecker import SpellChecker
import inflect

import difflib
import gensim

import pandas as pd

In [22]:
df = pd.read_csv("../data/usa_combined.csv")
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423591  got my first pfizer shot today. feeling well g...
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[423595 rows x 1 columns]

In [3]:
df.drop_duplicates(keep='first', inplace=True)

In [23]:
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423591  got my first pfizer shot today. feeling well g...
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[423595 rows x 1 columns]

## Used hashtags

In [5]:
text = df['Text']
hashtag_list = []
for tweet in text:
#     print(tweet)
    hashtags = re.findall("#[A-Za-z0-9_]+", tweet)
    if len(hashtags) > 0:
        for tag in hashtags:
            hashtag_list.append(tag)

In [6]:
hashtag_list

['#covidvaccineconfidence',
 '#vanguardvaccinationproject',
 '#populationcontrol',
 '#omicron',
 '#vaccination',
 '#mentalhealth',
 '#psychtwitter',
 '#cdnpoli',
 '#onpoli',
 '#covid19',
 '#l',
 '#polqc',
 '#getvaccinated',
 '#vaccineswork',
 '#canada',
 '#superbowlmusicfest',
 '#socal',
 '#superbowlexperience',
 '#sblvi',
 '#hiringphenomenaltalent',
 '#security',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#legaultmustresign',
 '#legault',
 '#covid19',
 '#localnews',
 '#newsbreak',
 '#covid',
 '#defundcbc',
 '#defundbbc',
 '#nyc',
 '#godblessamerica',
 '#nonads',
 '#votehelenkicknadlerny10',
 '#dyk',
 '#fightflu',
 '#heartmonth',
 '#nowplaying',
 '#nowspinning',
 '#np',
 '#nowstreaming',
 '#subgenius',
 '#joerogan',
 '#antivaxxers',
 '#covidab',
 '#covid19',
 '#repnotrip',
 '#ableg',
 '#ciuss_mcq',
 '#covid19',
 '#ambulance',
 '#inacceptable',
 '#k',
 '#jdq',
 '#covid19',
 '#mybodymychoice',
 '#rosiebartonappreciationday',
 '#ohio',
 

## Emoji Processing

In [7]:
import pickle
from emot.emo_unicode import UNICODE_EMOJI, EMOTICONS_EMO

In [8]:
# # 'Emoji_Dict.p'- download link https://drive.google.com/open?id=1G1vIkkbqPBYPKHcQ8qy0G2zkoab2Qv4v
with open('./Emoji_Dict.p', 'rb') as fp:
    Emoji_Dict = pickle.load(fp)
Emoji_Dict = {v: k for k, v in Emoji_Dict.items()}

# # Function for converting emojis into word
def convert_emojis(text):
    for emot in UNICODE_EMOJI:
        text = text.replace(emot, "_".join(UNICODE_EMOJI[emot].replace(",","").replace(":","").split()))
    return text

In [9]:
# TEST: line of text before emoji processing
df["Text"][107]

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [10]:
# TEST: convert_emoji function
convert_emojis(df['Text'][107])

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [ ]:
# emoji processing on df["text"] column

df["Text"] = df["Text"].astype(str)
df["new_text"] = df["Text"].apply(convert_emojis)

In [ ]:
df["new_text"][107]

## Emoticon Processing

In [11]:
# 'Emoticon_Dict.p'- download link https://drive.google.com/open?id=1HDpafp97gCl9xZTQWMgP2kKK_NuhENlE
with open('./Emoticon_Dict.p', 'rb') as fp:
    Emoticon_Dict = pickle.load(fp)
    
# Function for converting emoticons into word
def convert_emoticons(text):
    for emot in EMOTICONS_EMO:
        text = text.replace(emot, "_".join(EMOTICONS_EMO[emot].replace(",","").replace(":","").split()))
    return text

In [47]:
# TEST: convert_emoticons function
sentence_listtext = "Hello :-) :-)"
convert_emoticons(sentence_listtext)

'Hello Happy_face_smiley Happy_face_smiley'

In [12]:
df["new_text"] = df["new_text"].apply(convert_emoticons)

In [13]:
df.head()

Text  \
0  want find way end racism try force people inje...   
1  this child almost died tetanus, spent months h...   
2  juste se rappeler m. leblanc la pression que l...   
3  you would expect cases rise significantly, cou...   
4  depends whether vaccination status is embedded...   

                                            new_text  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  juste se rappeler m. leblanc la pression que l...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [14]:
# to deal with utf-8 that pycld can't handle
import regex

RE_BAD_CHARS = regex.compile(r"\p{Cc}|\p{Cs}")

def remove_bad_chars(text):
    return RE_BAD_CHARS.sub("", text)

remove_bad_chars("A\x96 bad char")  # Cc category
# 'A bad char'

'A bad char'

In [15]:
df['new_text'] = df['new_text'].apply(remove_bad_chars)

## Detecting Languages

In [16]:
import pycld2 as cld2

tweets = df['new_text']
language = []

for each in tweets:
    text_content = each
    _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
    language.append(detected_language)

In [17]:
langs = []

for each in language:
    lang_detected = ""
    for i in range(0,len(each)):
        lang_extracted = each[i][2]
        if i != (len(each) - 1):
            lang_detected += lang_extracted + ", "
        else:
            lang_detected += lang_extracted
    langs.append(lang_detected)

In [18]:
langs

['ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'FRENCH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',


In [19]:
df['languages'] = langs
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
423588  if you are eligible, please pre- register covi...   
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
423594  we all have do our part end this pandemic— get...   

                                                 new_text languages  
0       want find way end racism try force people inje...   ENGLISH  
1       this child almost died tetanus, spent months h...   ENGLISH  
2       juste se rappeler m. leblanc la pression que l...    FRENCH  
3       you would expect cases rise significantly, cou...   ENGLISH  
4       depends whether vaccination status is embedded...   ENGLISH  
...                                                   ...       ...  
423588  if you are eligible, please pre- register covi...   ENGLISH  
423590  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH  
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   Unknown  
423593  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH  
423594  we all have do our part end this pandemic— get...   ENGLISH  

[404337 rows x 3 columns]

In [20]:
df[df['languages'] != 'ENGLISH'].head()
#check how many rows

Text  \
2   juste se rappeler m. leblanc la pression que l...   
13                                        vaccination   
15  1-je comprends exactement ce qui doit être com...   
35  environ 500 médecins spécialistes participaien...   
38  c'est bien dommage que ce soit un droit, leur ...   

                                             new_text languages  
2   juste se rappeler m. leblanc la pression que l...    FRENCH  
13                                        vaccination   Unknown  
15  1-je comprends exactement ce qui doit être com...    FRENCH  
35  environ 500 médecins spécialistes participaien...    FRENCH  
38  c'est bien dommage que ce soit un droit, leur ...    FRENCH

In [21]:
df[df['languages'] != 'ENGLISH']['new_text']

2         juste se rappeler m. leblanc la pression que l...
13                                              vaccination
15        1-je comprends exactement ce qui doit être com...
35        environ 500 médecins spécialistes participaien...
38        c'est bien dommage que ce soit un droit, leur ...
                                ...                        
423579                             ayep. #vaccinesaveslives
423582    continue wear your mask preferably double , ge...
423585        #vaccinated #vaccinesaveslives syringemicrobe
423586    #vaccine #maskup #vaccinesaveslives #vaccinesi...
423592    #fauciouchie #2 #vaccinated #vaccinesaveslives...
Name: new_text, Length: 56002, dtype: object

In [91]:
df[df['languages'] != 'ENGLISH']['new_text'][105977]

'it’s time you do your part this fight against covid we reward you your actions we are sure we together be victorious this fight with collective effort everyone raising_handsmedium_skin_tone #vaccinesaveslives #weareinthistogether #plasmadonation #spreadpositivity'

In [22]:
df.to_csv('usa_after_language_detection.csv')

## Language Translation

In [1]:
# df = pd.read_csv('../data/usa_after_language_detection.csv')

In [ ]:
from deep_translator import GoogleTranslator

non_english = df[df['languages'] != 'ENGLISH']['new_text']

translated = []

for each in non_english:
    translate = GoogleTranslator(source='auto', target='en').translate(each)
    translated.append(translate)

In [ ]:
translated

In [ ]:
#creating new_text column
df['new_text'] = df['Text']

In [ ]:
non_english = df[df['languages'] != 'ENGLISH']

In [ ]:
non_english.head()
#33981 rows

In [ ]:
indexes_list = non_english.index

In [ ]:
indexes_list

In [ ]:
len(indexes_list)

In [ ]:
# range_firstNum = start_range + start_batch

# new_indexes_list = []

# for num in indexes_list:
#     new = num - range_firstNum
#     new_indexes_list.append(new)

In [ ]:
for i in range(0,len(indexes_list)):
    index = indexes_list[i]
    df.iloc[index]['new_text'] = translated[i]

In [ ]:
#check that the new_text col to see to check that the initial non-english rows have been translated
df[df['languages'] != 'ENGLISH']

## Language Detection Part 2

In [ ]:
# import pycld2 as cld2

# reviews = df['new_text_after_translation']
# language2 = []

# for each in reviews:
#     text_content = each
#     _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
#     language2.append(detected_language)

In [ ]:
# langs2 = []

# for each in language2:
#     lang_detected = ""
#     for i in range(0,len(each)):
#         lang_extracted = each[i][2]
#         if i != (len(each) - 1):
#             lang_detected += lang_extracted + ", "
#         else:
#             lang_detected += lang_extracted
#     langs2.append(lang_detected)

In [ ]:
# langs2

In [ ]:
# df['new_languages'] = langs2

In [ ]:
# df.to_csv("usa-after-langdetectandtrans.csv")

In [ ]:
# non_english2 = df[df['new_languages'] != 'ENGLISH']
# non_english2

In [ ]:
#see how many still detected as non-english, brieflcheck is it rly non english
# non_english2.info()

In [ ]:
# non_english2.to_csv('non_english2.csv')

## Read df after translation (USA)

In [63]:
df = pd.read_csv('./df_after_translation_usa.csv')

In [64]:
df.head()

Unnamed: 0                                               Text  \
0           0  want find way end racism try force people inje...   
1           1  this child almost died tetanus, spent months h...   
2           2  juste se rappeler m. leblanc la pression que l...   
3           3  you would expect cases rise significantly, cou...   
4           4  depends whether vaccination status is embedded...   

                                            new_text languages  \
0  want find way end racism try force people inje...   ENGLISH   
1  this child almost died tetanus, spent months h...   ENGLISH   
2  juste se rappeler m. leblanc la pression que l...    FRENCH   
3  you would expect cases rise significantly, cou...   ENGLISH   
4  depends whether vaccination status is embedded...   ENGLISH   

                          new_text_after_translation  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  just remember mr. leblanc the pressure that th...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [65]:
df

Unnamed: 0                                               Text  \
0                0  want find way end racism try force people inje...   
1                1  this child almost died tetanus, spent months h...   
2                2  juste se rappeler m. leblanc la pression que l...   
3                3  you would expect cases rise significantly, cou...   
4                4  depends whether vaccination status is embedded...   
...            ...                                                ...   
404260      404260  if you are eligible, please pre- register covi...   
404261      404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262      404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263      404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264      404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 5 columns]

In [66]:
df.drop('Unnamed: 0', axis=1, inplace=True)

In [67]:
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
404260  if you are eligible, please pre- register covi...   
404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 4 columns]

## Text File & Corpus Creation

In [8]:
# create txt file for each text review

# def CreateCorpusFromDataFrame(corpusfolder, df):
#     for index, r in df.iterrows():
#     # print (r['text'])
#     # print (str(index) + '.txt')
#         text = r['new_text_after_translation']
#         fname = str(index)+'.txt'
#         corpusfile = open(corpusfolder+'/'+fname, "w", encoding="utf-8")
#         corpusfile.write(str(text))
#         corpusfile.close()

# CreateCorpusFromDataFrame('../text-corpus-usa-v2', df)

# reference: https://stackoverflow.com/questions/49088978/how-to-create-corpus-from-pandas-data-frame-to-operate-with-nltk/49104725

In [2]:
file_directory = '../../text-corpus-usa-v2'
filename_pattern = '.+\.txt'

my_corpus = PlaintextCorpusReader(file_directory, filename_pattern)

#Print some words in specific file
test = my_corpus.words('0.txt')
print(test)
print(len(test))

['want', 'find', 'way', 'end', 'racism', 'try', ...]
52


In [3]:
#Total number of text files i.e. total number of tweets
print(len(my_corpus.fileids()))

404265


In [4]:
fdist = nltk.FreqDist(test)
print(fdist.most_common(10))

[('people', 4), ('.', 4), ('i', 3), ('force', 2), ('against', 2), ('vaxx', 2), ('want', 1), ('find', 1), ('way', 1), ('end', 1)]


In [5]:
# word distribution across all files
fdist_all_files = nltk.FreqDist(my_corpus.words())
print(fdist_all_files.most_common(10))

[('.', 610203), (',', 312331), ('i', 202578), ('’', 157035), ('is', 141760), ('#', 133834), ("'", 132757), ('it', 131106), ('you', 126725), ('that', 120183)]


In [6]:
#total number of words
total_words = my_corpus.words()
print(total_words)
print(len(total_words))

['want', 'find', 'way', 'end', 'racism', 'try', ...]
11384323


## Tokenization

In [7]:
#Creating a sorted list of texts since my_corpus.fileids() does not read texts consecutively
#EDIT RANGE
sorted_list = [f'{i}.txt' for i in range(60000, 65000)]

In [8]:
tokenised_words = [my_corpus.words(each) for each in sorted_list]
tokenised_words

[['when', 'i', 'got', 'my', 'booster', 'there', 'was', ...],
 ['they', 'been', 'lying', 'us', ',', 'fauci', ',', ...],
 ['another', 'good', 'one', 'for', 'you', 'here', '.', ...],
 ['i', 'had', 'pfizer', 'booster', 'with', 'no', 'side', ...],
 ['#', 'crimesagainsthumanity', 'will', 'not', 'go', ...],
 ['if', 'life', 'is', '“', 'priceless', '”', 'it', '’', ...],
 ['look', 'at', 'how', 'it', 'was', 'developed', 'by', ...],
 ['i', "'", 'm', 'house', 'pfizer', 'as', 'well', '.', ...],
 ['pfizer', 'hit', 'me', 'much', 'harder', 'than', 'it', ...],
 ['hopefully', 'some', 'powerful', 'people', 'brought', ...],
 ['i', 'took', 'my', 'pfizer', 'booster', 'late', ...],
 ['it', 'was', 'teddy', 'bear', 'transport', 'cook', ...],
 ['that', 'is', 'false', ',', 'pfizer', ',', 'modern', ...],
 ['i', 'wish', 'you', 'would', 'screen', 'cap', ...],
 ['pfizer', 'disagrees', 'with', 'your', 'last', ...],
 ['i', 'can', 'say', 'that', 'my', 'az', '1st', ...],
 ['Good', 'morning', ',', 'if', 'I', 'have', 'my',

In [9]:
print(len(tokenised_words))

5000


## Converting British to American English

In [10]:
#https://stackoverflow.com/questions/42329766/python-nlp-british-english-vs-american-english

import requests

def americanize(word):
    url ="https://raw.githubusercontent.com/hyperreality/American-British-English-Translator/master/data/british_spellings.json"
    british_to_american_dict = requests.get(url).json()

    for british_spelling, american_spelling in british_to_american_dict.items():
        word = word.replace(british_spelling, american_spelling)
  
    return word

In [11]:
test_americanize = [['flavour', 'colour'], ['apologise', 'travelled']]
test_americanize = [[americanize(w) for w in each] for each in test_americanize]
test_americanize

[['flavor', 'color'], ['apologize', 'traveled']]

In [12]:
tokenised = [[americanize(w) for w in each] for each in tokenised_words]
tokenised

[['when',
  'i',
  'got',
  'my',
  'booster',
  'there',
  'was',
  'like',
  '15',
  'different',
  'pharmacies',
  'close',
  'me',
  'offering',
  'pfizer',
  'but',
  'i',
  'had',
  'already',
  'had',
  'moderna',
  'so',
  'i',
  'drove',
  'like',
  'twenty',
  'minutes',
  'closest',
  'moderna',
  'place',
  '.',
  'it',
  'was',
  'hood',
  '.',
  'i',
  'regret',
  'nothing'],
 ['they',
  'been',
  'lying',
  'us',
  ',',
  'fauci',
  ',',
  'pfizer',
  'biden',
  'since',
  'beginning',
  'biden',
  "'",
  's',
  'term',
  'still',
  'are',
  'not',
  'telling',
  'us',
  ',',
  'are',
  'vaccines',
  'no',
  'good',
  ',',
  'are',
  'they',
  'destroying',
  'our',
  'immune',
  'systems',
  ',',
  'has',
  'china',
  'released',
  'another',
  'killer',
  'covid',
  'what',
  "'",
  's',
  'fucking',
  'truth'],
 ['another',
  'good',
  'one',
  'for',
  'you',
  'here',
  '.',
  'take',
  'a',
  'look',
  '.',
  'about',
  'pfizer',
  '.'],
 ['i',
  'had',
  'pfizer',

In [13]:
# save americanized tokens
convert_to_str = []

for each in tokenised:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('usa_americanized_60k-65k.csv')

## Conversion to numerals

In [14]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised)

True

In [15]:
# since theres numbers, the numbers need to be converted to words e.g. "2" to "two"

p = inflect.engine()
  
# convert number into words
def convert_number(text):
    # split string into list of words
    temp_str = text.split()
    # initialise empty list
    new_string = []
  
    for word in temp_str:
        # if word is a digit, convert the digit
        # to numbers and append into the new_string list
        if word.isdigit():
            temp = p.number_to_words(word)
            new_string.append(temp)
  
        # append the word as it is
        else:
            new_string.append(word)
  
    # join the words of new_string to form a string
    temp_str = ' '.join(new_string)
    return temp_str

In [16]:
# example text which contain numbers in it
input_list = ['There are 3 balls in this bag, and 12 in the other one.', '29']
result = [convert_number(each)for each in input_list]
result

['There are three balls in this bag, and twelve in the other one.',
 'twenty-nine']

In [17]:
#NEED TO CHANGE VARIABLE after us to brit eng conversion

tokenised_numerals_converted = [[convert_number(w) for w in each] for each in tokenised]

In [18]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised_numerals_converted)

False

## Misspellings

In [19]:
def correct_typo(tokens):
    spell = SpellChecker()
    return [spell.correction(t) if len(spell.unknown([t]))>0 else t for t in tokens]

In [20]:
misspelled_test = ['greot', 'coyor', 'and', 'misspeling']
correct_typo(misspelled_test)

['great', 'color', 'and', 'misspelling']

In [21]:
tokenised_spellchecked = [correct_typo(each) for each in tokenised_numerals_converted]

In [22]:
tokenised_spellchecked

[['when',
  'i',
  'got',
  'my',
  'booster',
  'there',
  'was',
  'like',
  'fifteen',
  'different',
  'pharmacies',
  'close',
  'me',
  'offering',
  'pfizer',
  'but',
  'i',
  'had',
  'already',
  'had',
  'modern',
  'so',
  'i',
  'drove',
  'like',
  'twenty',
  'minutes',
  'closest',
  'modern',
  'place',
  '.',
  'it',
  'was',
  'hood',
  '.',
  'i',
  'regret',
  'nothing'],
 ['they',
  'been',
  'lying',
  'us',
  ',',
  'faci',
  ',',
  'pfizer',
  'biden',
  'since',
  'beginning',
  'biden',
  "'",
  'i',
  'term',
  'still',
  'are',
  'not',
  'telling',
  'us',
  ',',
  'are',
  'vaccines',
  'no',
  'good',
  ',',
  'are',
  'they',
  'destroying',
  'our',
  'immune',
  'systems',
  ',',
  'has',
  'china',
  'released',
  'another',
  'killer',
  'couid',
  'what',
  "'",
  'i',
  'fucking',
  'truth'],
 ['another',
  'good',
  'one',
  'for',
  'you',
  'here',
  '.',
  'take',
  'a',
  'look',
  '.',
  'about',
  'pfizer',
  '.'],
 ['i',
  'had',
  'pfizer

In [23]:
convert_to_str = []

for each in tokenised_spellchecked:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('usa_corrected_60k-65k.csv')

## Compiled CSV

In [2]:
df2 = pd.read_csv("./usa_compiled_242_322k.csv")
df2

0
0      also, ,, like, not, get, morbid, here, ,, but,...
1      couid, has, gotten, so, bad, that, someone, is...
2      wake, up, everyone, ..., do, you, see, what, '...
3      along, with, anyone, who, is, immunocompromise...
4      living, with, crown, i, i, disease, can, be, s...
...                                                  ...
79995  i, know, healthy, man, who, was, not, vaccinat...
79996  no, ,, if, they, don, i, i, like, it, they, ca...
79997  there, are, documented, cases, but, not, sure,...
79998                                               gone
79999  him, ., this, sounds, bit, familiar, ., you, s...

[80000 rows x 1 columns]

In [3]:
new_tokenised_spellchecked = []

for row in df2['0']:
    alist = row.split(", ")
    new_tokenised_spellchecked.append(alist)

In [4]:
new_tokenised_spellchecked

[['also',
  ',',
  'like',
  'not',
  'get',
  'morbid',
  'here',
  ',',
  'but',
  'one',
  'players',
  'with',
  'couid',
  'steelers',
  'immunocompromised',
  '.',
  'like',
  '...',
  'ink',
  'let',
  "'",
  'i',
  'have',
  'some',
  'perspective',
  '.'],
 ['couid',
  'has',
  'gotten',
  'so',
  'bad',
  'that',
  'someone',
  'is',
  'now',
  'living',
  'my',
  'garage',
  '.',
  'their',
  'roommates',
  'were',
  'not',
  'taking',
  'precautions',
  '.',
  'they',
  'are',
  'immunocompromised',
  '.',
  'their',
  'roommates',
  'are',
  'assholes',
  '.'],
 ['wake',
  'up',
  'everyone',
  '...',
  'do',
  'you',
  'see',
  'what',
  "'",
  'i',
  'happening',
  'here',
  'is',
  'couid',
  'dangerous',
  'those',
  'immunocompromised',
  'absolutely',
  '.',
  'however',
  ',',
  'fun',
  'fact',
  ':',
  'so',
  'is',
  'common',
  'cold',
  'flu',
  'both',
  'caused',
  'by',
  'coronavirus',
  'bow',
  '.',
  'i',
  'can',
  "'",
  'i',
  'wear',
  'mask',
  'pro

## Convert to lowercase

In [5]:
# #NEED TO CHANGE VARIABLE AFTER SPELLCHECK

# tokenised_lower = [[w.lower() for w in each] for each in tokenised_numerals_converted]
# tokenised_lower

## Remove punctuation

In [6]:
# remove punctuations from tokenised_lower
tokenised_words_only = [[w for w in each if re.search('^[a-z]+$',w)] for each in new_tokenised_spellchecked]
tokenised_words_only

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'here',
  'but',
  'one',
  'players',
  'with',
  'couid',
  'steelers',
  'immunocompromised',
  'like',
  'ink',
  'let',
  'i',
  'have',
  'some',
  'perspective'],
 ['couid',
  'has',
  'gotten',
  'so',
  'bad',
  'that',
  'someone',
  'is',
  'now',
  'living',
  'my',
  'garage',
  'their',
  'roommates',
  'were',
  'not',
  'taking',
  'precautions',
  'they',
  'are',
  'immunocompromised',
  'their',
  'roommates',
  'are',
  'assholes'],
 ['wake',
  'up',
  'everyone',
  'do',
  'you',
  'see',
  'what',
  'i',
  'happening',
  'here',
  'is',
  'couid',
  'dangerous',
  'those',
  'immunocompromised',
  'absolutely',
  'however',
  'fun',
  'fact',
  'so',
  'is',
  'common',
  'cold',
  'flu',
  'both',
  'caused',
  'by',
  'coronavirus',
  'bow',
  'i',
  'can',
  'i',
  'wear',
  'mask',
  'prolonged',
  'periods',
  'due',
  'health',
  'concerns',
  'but',
  'i',
  'one'],
 ['along',
  'with',
  'anyone',
  'who'

## POS Tagging

In [7]:
# tokens = tokenised_words_only[0]
# tokens

In [8]:
# nltk.pos_tag(tokens)

In [9]:
pos_tagged = []

for each in tokenised_words_only:
    pos_tags = nltk.pos_tag(each)
    pos_tagged.append(pos_tags)

In [10]:
pos_tagged

[[('also', 'RB'),
  ('like', 'IN'),
  ('not', 'RB'),
  ('get', 'VB'),
  ('morbid', 'NN'),
  ('here', 'RB'),
  ('but', 'CC'),
  ('one', 'CD'),
  ('players', 'NNS'),
  ('with', 'IN'),
  ('couid', 'NN'),
  ('steelers', 'NNS'),
  ('immunocompromised', 'VBD'),
  ('like', 'IN'),
  ('ink', 'NN'),
  ('let', 'NN'),
  ('i', 'NN'),
  ('have', 'VBP'),
  ('some', 'DT'),
  ('perspective', 'NN')],
 [('couid', 'NN'),
  ('has', 'VBZ'),
  ('gotten', 'VBN'),
  ('so', 'RB'),
  ('bad', 'JJ'),
  ('that', 'IN'),
  ('someone', 'NN'),
  ('is', 'VBZ'),
  ('now', 'RB'),
  ('living', 'VBG'),
  ('my', 'PRP$'),
  ('garage', 'NN'),
  ('their', 'PRP$'),
  ('roommates', 'NNS'),
  ('were', 'VBD'),
  ('not', 'RB'),
  ('taking', 'VBG'),
  ('precautions', 'NNS'),
  ('they', 'PRP'),
  ('are', 'VBP'),
  ('immunocompromised', 'VBN'),
  ('their', 'PRP$'),
  ('roommates', 'NNS'),
  ('are', 'VBP'),
  ('assholes', 'NNS')],
 [('wake', 'VB'),
  ('up', 'RP'),
  ('everyone', 'NN'),
  ('do', 'VB'),
  ('you', 'PRP'),
  ('see', 'VB'),


In [11]:
#IMPORT BACK THE ORIGINAL DF

# import pandas as pd

df = pd.read_csv("./df_after_translation_usa.csv")

In [13]:
df.drop(columns="Unnamed: 0", inplace = True)

In [14]:
df = df.iloc[242000:322000]

In [15]:
df

Text  \
242000  also, like not get morbid here, but one player...   
242001  covid has gotten so bad that someone is now li...   
242002  wake up everyone... do you see what's happenin...   
242003  along with anyone who is immunocompromised, ho...   
242004  living with crohn’s disease can be struggle. b...   
...                                                   ...   
321995  i know healthy man who was not vaccinated. he ...   
321996  no, if they don’t like it they can choose diff...   
321997  there are documented cases but not sure how mu...   
321998                                             partée   
321999  hmm. this sounds bit familiar. you shouldn't f...   

                                                 new_text languages  \
242000  also, like not get morbid here, but one player...   ENGLISH   
242001  covid has gotten so bad that someone is now li...   ENGLISH   
242002  wake up everyone... do you see what's happenin...   ENGLISH   
242003  along with anyone who is immunocompromised, ho...   ENGLISH   
242004  living with crohn’s disease can be struggle. b...   ENGLISH   
...                                                   ...       ...   
321995  i know healthy man who was not vaccinated. he ...   ENGLISH   
321996  no, if they don’t like it they can choose diff...   ENGLISH   
321997  there are documented cases but not sure how mu...   ENGLISH   
321998                                             partée   Unknown   
321999  hmm. this sounds bit familiar. you shouldn't f...   ENGLISH   

                               new_text_after_translation  
242000  also, like not get morbid here, but one player...  
242001  covid has gotten so bad that someone is now li...  
242002  wake up everyone... do you see what's happenin...  
242003  along with anyone who is immunocompromised, ho...  
242004  living with crohn’s disease can be struggle. b...  
...                                                   ...  
321995  i know healthy man who was not vaccinated. he ...  
321996  no, if they don’t like it they can choose diff...  
321997  there are documented cases but not sure how mu...  
321998                                               gone  
321999  hmm. this sounds bit familiar. you shouldn't f...  

[80000 rows x 4 columns]

In [16]:
df['pos_tagged_words'] = pos_tagged

/var/folders/c2/cm91y7kj44lc8pmlxymc3dr40000gn/T/ipykernel_41189/1355882041.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['pos_tagged_words'] = pos_tagged


In [17]:
df.head()

Text  \
242000  also, like not get morbid here, but one player...   
242001  covid has gotten so bad that someone is now li...   
242002  wake up everyone... do you see what's happenin...   
242003  along with anyone who is immunocompromised, ho...   
242004  living with crohn’s disease can be struggle. b...   

                                                 new_text languages  \
242000  also, like not get morbid here, but one player...   ENGLISH   
242001  covid has gotten so bad that someone is now li...   ENGLISH   
242002  wake up everyone... do you see what's happenin...   ENGLISH   
242003  along with anyone who is immunocompromised, ho...   ENGLISH   
242004  living with crohn’s disease can be struggle. b...   ENGLISH   

                               new_text_after_translation  \
242000  also, like not get morbid here, but one player...   
242001  covid has gotten so bad that someone is now li...   
242002  wake up everyone... do you see what's happenin...   
242003  along with anyone who is immunocompromised, ho...   
242004  living with crohn’s disease can be struggle. b...   

                                         pos_tagged_words  
242000  [(also, RB), (like, IN), (not, RB), (get, VB),...  
242001  [(couid, NN), (has, VBZ), (gotten, VBN), (so, ...  
242002  [(wake, VB), (up, RP), (everyone, NN), (do, VB...  
242003  [(along, IN), (with, IN), (anyone, NN), (who, ...  
242004  [(living, VBG), (with, IN), (crown, JJ), (i, N...

## Stop word removal

In [ ]:
# # TEST: remove stop words from test_words_only
# from nltk.corpus import stopwords
# stop_list = stopwords.words('english')

# test_words_only1 = ['not', 'great', 'color', 'and', 'cruelty', 'free', 'i', 'use', 'elf', 'cosmetics', 'every', 'day', 'and', 'i', 'love', 'it']
# test_stopremoved = [w for w in test_words_only1 if w not in stop_list or w == 'not']
# print(test_stopremoved)

In [18]:
# remove stop words from tokenised_words_only
from nltk.corpus import stopwords
stop_list = stopwords.words('english')
tokenised_stopremoved = [[w for w in each if w not in stop_list or w == 'not'] for each in tokenised_words_only]
tokenised_stopremoved

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'one',
  'players',
  'couid',
  'steelers',
  'immunocompromised',
  'like',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'gotten',
  'bad',
  'someone',
  'living',
  'garage',
  'roommates',
  'not',
  'taking',
  'precautions',
  'immunocompromised',
  'roommates',
  'assholes'],
 ['wake',
  'everyone',
  'see',
  'happening',
  'couid',
  'dangerous',
  'immunocompromised',
  'absolutely',
  'however',
  'fun',
  'fact',
  'common',
  'cold',
  'flu',
  'caused',
  'coronavirus',
  'bow',
  'wear',
  'mask',
  'prolonged',
  'periods',
  'due',
  'health',
  'concerns',
  'one'],
 ['along', 'anyone', 'immunocompromised', 'remotely', 'question'],
 ['living',
  'crown',
  'disease',
  'struggle',
  'immunocompromised',
  'pandemic',
  'due',
  'medication',
  'even',
  'bigger',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['hiv',
  'many',

## Bigram & Trigram Models

In [19]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(tokenised_stopremoved, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[tokenised_stopremoved], threshold=100)
# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

In [20]:
def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]
def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

In [21]:
# Form Bigrams
tokenised_bigrams = make_bigrams(tokenised_stopremoved)
# Form Trigrams
tokenised_trigrams = make_trigrams(tokenised_stopremoved)

In [22]:
tokenised_bigrams

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'one',
  'players',
  'couid',
  'steelers',
  'immunocompromised',
  'like',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'gotten',
  'bad',
  'someone',
  'living',
  'garage',
  'roommates',
  'not',
  'taking',
  'precautions',
  'immunocompromised',
  'roommates',
  'assholes'],
 ['wake',
  'everyone',
  'see',
  'happening',
  'couid',
  'dangerous',
  'immunocompromised',
  'absolutely',
  'however',
  'fun',
  'fact',
  'common_cold',
  'flu',
  'caused',
  'coronavirus',
  'bow',
  'wear',
  'mask',
  'prolonged',
  'periods',
  'due',
  'health',
  'concerns',
  'one'],
 ['along', 'anyone', 'immunocompromised', 'remotely', 'question'],
 ['living',
  'crown',
  'disease',
  'struggle',
  'immunocompromised',
  'pandemic',
  'due',
  'medication',
  'even',
  'bigger',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['hiv',
  'many',
  'f

In [23]:
tokenised_trigrams

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'one',
  'players',
  'couid',
  'steelers',
  'immunocompromised',
  'like',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'gotten',
  'bad',
  'someone',
  'living',
  'garage',
  'roommates',
  'not',
  'taking',
  'precautions',
  'immunocompromised',
  'roommates',
  'assholes'],
 ['wake',
  'everyone',
  'see',
  'happening',
  'couid',
  'dangerous',
  'immunocompromised',
  'absolutely',
  'however',
  'fun',
  'fact',
  'common_cold',
  'flu',
  'caused',
  'coronavirus',
  'bow',
  'wear',
  'mask',
  'prolonged',
  'periods',
  'due',
  'health',
  'concerns',
  'one'],
 ['along', 'anyone', 'immunocompromised', 'remotely', 'question'],
 ['living',
  'crown',
  'disease',
  'struggle',
  'immunocompromised',
  'pandemic',
  'due',
  'medication',
  'even',
  'bigger',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['hiv',
  'many',
  'f

## Lemmatization

### Lemmatization with all postags

In [24]:
def lemmatization_all(texts):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc])
    return texts_out

In [25]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

tokenised_lemmatized_1 = lemmatization_all(tokenised_bigrams)
tokenised_lemmatized_1

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'one',
  'player',
  'couid',
  'steeler',
  'immunocompromise',
  'like',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'get',
  'bad',
  'someone',
  'live',
  'garage',
  'roommate',
  'not',
  'take',
  'precaution',
  'immunocompromise',
  'roommate',
  'asshole'],
 ['wake',
  'everyone',
  'see',
  'happen',
  'couid',
  'dangerous',
  'immunocompromise',
  'absolutely',
  'however',
  'fun',
  'fact',
  'common_cold',
  'flu',
  'cause',
  'coronavirus',
  'bow',
  'wear',
  'mask',
  'prolong',
  'period',
  'due',
  'health',
  'concern',
  'one'],
 ['along', 'anyone', 'immunocompromise', 'remotely', 'question'],
 ['live',
  'crown',
  'disease',
  'struggle',
  'immunocompromise',
  'pandemic',
  'due',
  'medication',
  'even',
  'big',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['hiv',
  'many',
  'face',
  'one',
  'happy',
  'wo

### Lemmatisation with noun, adj, verb and adv

In [26]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [27]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_2 = lemmatization(tokenised_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])
tokenised_lemmatized_2

[['also',
  'morbid',
  'player',
  'couid',
  'steeler',
  'immunocompromise',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'get',
  'bad',
  'live',
  'garage',
  'roommate',
  'take',
  'precaution',
  'immunocompromise',
  'roommate',
  'asshole'],
 ['wake',
  'see',
  'happen',
  'couid',
  'dangerous',
  'immunocompromise',
  'absolutely',
  'however',
  'fun',
  'fact',
  'flu',
  'cause',
  'bow',
  'wear',
  'mask',
  'prolong',
  'period',
  'due',
  'health',
  'concern'],
 ['immunocompromise', 'remotely', 'question'],
 ['live',
  'struggle',
  'immunocompromise',
  'pandemic',
  'due',
  'medication',
  'even',
  'big',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['many',
  'face',
  'happy',
  'worldaidsday',
  'let',
  'end',
  'shame',
  'celebrate',
  'resilience',
  'sake',
  'immunocompromise',
  'people',
  'everywhere',
  'wear',
  'eff',
  'mask'],
 ['real',
  'problem',
 

### Lemmatisation with nouns only

In [28]:
def lemmatization_noun(texts, allowed_postags=['NOUN']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [29]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_3 = lemmatization_noun(tokenised_bigrams, allowed_postags=['NOUN'])
tokenised_lemmatized_3

[['morbid', 'player', 'couid', 'steeler', 'ink', 'perspective'],
 ['couid', 'garage', 'roommate', 'precaution', 'roommate', 'asshole'],
 ['couid', 'fact', 'flu', 'wear', 'mask', 'period', 'health', 'concern'],
 ['question'],
 ['struggle', 'medication', 'struggle', 'people', 'sun'],
 ['worldaidsday', 'end', 'shame', 'resilience', 'sake', 'people', 'mask'],
 ['problem',
  'research',
  'amp',
  'farce',
  'year',
  'research',
  'health',
  'state',
  'health',
  'amp',
  'wish',
  'work'],
 ['obese'],
 ['story', 'state', 'couid', 'work', 'health', 'business'],
 ['way', 'die', 'death'],
 ['illness', 'illness', 'condition', 'death', 'couid', 'couid', 'kill'],
 ['vaccination'],
 ['lasix'],
 ['review', 'makes_sense', 'plan', 'year', 'cancerpaitent'],
 ['reason', 'app', 'place', 'system'],
 ['support', 'establishment', 'refuse', 'refuse', 'risk', 'risk', 'person'],
 ['vaccine', 'year', 'reason'],
 ['car',
  'license',
  'life',
  'vaccine',
  'arm',
  'travel',
  'work',
  'rule',
  'couid',

### Gibberish Remover

In [ ]:
# #test
# trial_nested=[['happy', 'time', 'ajsdnkfjak'],[],[],['dsnfkajka','yo','wassup']]

In [ ]:
# #test
# len([])

# if len([])== False:
#     print('hi')

In [ ]:
# #test
# from gibberish_detector import detector
# # load the gibberish detection model
# Detector = detector.create_from_model('../Gibberish-Detector-master/gibberish-detector.model')

# ##change variable tokenised_lemmatized_x

# new_list = []

# for alist in trial_nested:
#     mini_list = []
#     if len(alist):
#         for word in alist:
#             test = Detector.is_gibberish(word)
#             if test == False:
#                 mini_list.append(word)
#     new_list.append(mini_list)

In [ ]:
# #test
# new_list

In [30]:
#this is for tokenised_lemmatized_1
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list = []

for alist in tokenised_lemmatized_1:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list.append(mini_list)
    
tokenised_lemmatized_1 = new_list

In [31]:
tokenised_lemmatized_1

[['also',
  'like',
  'not',
  'get',
  'morbid',
  'one',
  'player',
  'couid',
  'steeler',
  'immunocompromise',
  'like',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'get',
  'bad',
  'someone',
  'live',
  'garage',
  'roommate',
  'not',
  'take',
  'precaution',
  'immunocompromise',
  'roommate',
  'asshole'],
 ['wake',
  'everyone',
  'see',
  'happen',
  'couid',
  'dangerous',
  'immunocompromise',
  'absolutely',
  'however',
  'fun',
  'fact',
  'common_cold',
  'flu',
  'cause',
  'coronavirus',
  'bow',
  'wear',
  'mask',
  'prolong',
  'period',
  'due',
  'health',
  'concern',
  'one'],
 ['along', 'anyone', 'immunocompromise', 'remotely', 'question'],
 ['live',
  'crown',
  'disease',
  'struggle',
  'immunocompromise',
  'pandemic',
  'due',
  'medication',
  'even',
  'big',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['hiv',
  'many',
  'face',
  'one',
  'happy',
  'wo

In [32]:
#this is for tokenised_lemmatized_2
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list2 = []

for alist in tokenised_lemmatized_2:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list2.append(mini_list)
                
tokenised_lemmatized_2 = new_list2

In [33]:
tokenised_lemmatized_2

[['also',
  'morbid',
  'player',
  'couid',
  'steeler',
  'immunocompromise',
  'ink',
  'let',
  'perspective'],
 ['couid',
  'get',
  'bad',
  'live',
  'garage',
  'roommate',
  'take',
  'precaution',
  'immunocompromise',
  'roommate',
  'asshole'],
 ['wake',
  'see',
  'happen',
  'couid',
  'dangerous',
  'immunocompromise',
  'absolutely',
  'however',
  'fun',
  'fact',
  'flu',
  'cause',
  'bow',
  'wear',
  'mask',
  'prolong',
  'period',
  'due',
  'health',
  'concern'],
 ['immunocompromise', 'remotely', 'question'],
 ['live',
  'struggle',
  'immunocompromise',
  'pandemic',
  'due',
  'medication',
  'even',
  'big',
  'struggle',
  'lucky',
  'many',
  'supportive',
  'people',
  'side',
  'sun',
  'crohnsandcolitisawarenessweek',
  'invisible'],
 ['many',
  'face',
  'happy',
  'worldaidsday',
  'let',
  'end',
  'shame',
  'celebrate',
  'resilience',
  'sake',
  'immunocompromise',
  'people',
  'everywhere',
  'wear',
  'eff',
  'mask'],
 ['real',
  'problem',
 

In [34]:
#this is for tokenised_lemmatized_3
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list3 = []

for alist in tokenised_lemmatized_3:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list3.append(mini_list)
                
tokenised_lemmatized_3 = new_list3

In [35]:
tokenised_lemmatized_3

[['morbid', 'player', 'couid', 'steeler', 'ink', 'perspective'],
 ['couid', 'garage', 'roommate', 'precaution', 'roommate', 'asshole'],
 ['couid', 'fact', 'flu', 'wear', 'mask', 'period', 'health', 'concern'],
 ['question'],
 ['struggle', 'medication', 'struggle', 'people', 'sun'],
 ['worldaidsday', 'end', 'shame', 'resilience', 'sake', 'people', 'mask'],
 ['problem',
  'research',
  'amp',
  'farce',
  'year',
  'research',
  'health',
  'state',
  'health',
  'amp',
  'wish',
  'work'],
 ['obese'],
 ['story', 'state', 'couid', 'work', 'health', 'business'],
 ['way', 'die', 'death'],
 ['illness', 'illness', 'condition', 'death', 'couid', 'couid', 'kill'],
 ['vaccination'],
 ['lasix'],
 ['review', 'makes_sense', 'plan', 'year', 'cancerpaitent'],
 ['reason', 'app', 'place', 'system'],
 ['support', 'establishment', 'refuse', 'refuse', 'risk', 'risk', 'person'],
 ['vaccine', 'year', 'reason'],
 ['car',
  'license',
  'life',
  'vaccine',
  'arm',
  'travel',
  'work',
  'rule',
  'couid',

## Creating column with Pre-processed words

In [36]:
df["words_processed_all"] = tokenised_lemmatized_1
df["words_processed_noun_adj_verb_adv"] = tokenised_lemmatized_2
df["words_processed_noun"] = tokenised_lemmatized_3

/var/folders/c2/cm91y7kj44lc8pmlxymc3dr40000gn/T/ipykernel_41189/3714202619.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["words_processed_all"] = tokenised_lemmatized_1
/var/folders/c2/cm91y7kj44lc8pmlxymc3dr40000gn/T/ipykernel_41189/3714202619.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["words_processed_noun_adj_verb_adv"] = tokenised_lemmatized_2
/var/folders/c2/cm91y7kj44lc8pmlxymc3dr40000gn/T/ipykernel_41189/3714202619.py:3: SettingWithCopyWarning: 
A value is trying to be set on a 

In [37]:
df.head()

Text  \
242000  also, like not get morbid here, but one player...   
242001  covid has gotten so bad that someone is now li...   
242002  wake up everyone... do you see what's happenin...   
242003  along with anyone who is immunocompromised, ho...   
242004  living with crohn’s disease can be struggle. b...   

                                                 new_text languages  \
242000  also, like not get morbid here, but one player...   ENGLISH   
242001  covid has gotten so bad that someone is now li...   ENGLISH   
242002  wake up everyone... do you see what's happenin...   ENGLISH   
242003  along with anyone who is immunocompromised, ho...   ENGLISH   
242004  living with crohn’s disease can be struggle. b...   ENGLISH   

                               new_text_after_translation  \
242000  also, like not get morbid here, but one player...   
242001  covid has gotten so bad that someone is now li...   
242002  wake up everyone... do you see what's happenin...   
242003  along with anyone who is immunocompromised, ho...   
242004  living with crohn’s disease can be struggle. b...   

                                         pos_tagged_words  \
242000  [(also, RB), (like, IN), (not, RB), (get, VB),...   
242001  [(couid, NN), (has, VBZ), (gotten, VBN), (so, ...   
242002  [(wake, VB), (up, RP), (everyone, NN), (do, VB...   
242003  [(along, IN), (with, IN), (anyone, NN), (who, ...   
242004  [(living, VBG), (with, IN), (crown, JJ), (i, N...   

                                      words_processed_all  \
242000  [also, like, not, get, morbid, one, player, co...   
242001  [couid, get, bad, someone, live, garage, roomm...   
242002  [wake, everyone, see, happen, couid, dangerous...   
242003  [along, anyone, immunocompromise, remotely, qu...   
242004  [live, crown, disease, struggle, immunocomprom...   

                        words_processed_noun_adj_verb_adv  \
242000  [also, morbid, player, couid, steeler, immunoc...   
242001  [couid, get, bad, live, garage, roommate, take...   
242002  [wake, see, happen, couid, dangerous, immunoco...   
242003             [immunocompromise, remotely, question]   
242004  [live, struggle, immunocompromise, pandemic, d...   

                                     words_processed_noun  
242000  [morbid, player, couid, steeler, ink, perspect...  
242001  [couid, garage, roommate, precaution, roommate...  
242002  [couid, fact, flu, wear, mask, period, health,...  
242003                                         [question]  
242004      [struggle, medication, struggle, people, sun]

In [ ]:
df.to_csv('usa_preprocessed_242_322k.csv')

## TFIDF

In [ ]:
df['words_processed_all']

In [ ]:
def listToString(s): 
    # initialize an empty string
    str1 = "" 
    # traverse in the string  
    for ele in s: 
        str1 += ele  
    # return string  
    return str1

In [ ]:
newlist = []

for each in df['words_processed_all']:
    new = each.strip("][").replace("'","").split(", ")
    newlist.append(new)

In [ ]:
newlist

In [ ]:
joined_list = []

for lis in newlist:
    new = " ".join(lis)
    joined_list.append(new)

In [ ]:
joined_list

In [ ]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
import pandas as pd
cv = CountVectorizer()
word_count_vector = cv.fit_transform(joined_list)
tf = pd.DataFrame(word_count_vector.toarray(), columns=cv.get_feature_names())
print(tf)

In [ ]:
tfidf_transformer = TfidfTransformer()
X = tfidf_transformer.fit_transform(word_count_vector)
idf = pd.DataFrame({'feature_name':cv.get_feature_names(), 'idf_weights':tfidf_transformer.idf_})
idf.sort_values('idf_weights', ascending=False, inplace=True)

In [ ]:
idf.to_csv('tfidf-descending.csv')

In [ ]:
tf_idf = pd.DataFrame(X.toarray(),columns=cv.get_feature_names())
tf_idf